In [ ]:
import pandas as pd
import numpy as np
from pathlib import Path

# ===== Load Data =====
folder_path = Path("data")  # Make sure there's a 'data/' folder next to this script

building_years = []
for year in range(2015, 2020):
    df = pd.read_csv(folder_path / f'building_details_{year}.csv')  # FIXED
    df['year'] = year
    building_years.append(df)

building_all = pd.concat(building_years, ignore_index=True)
building_all = building_all.drop_duplicates(subset=['acct', 'year'], keep='first')
pivoted = building_all.pivot(index='acct', columns='year')
pivoted.columns = [f'{col}_{year}' for col, year in pivoted.columns]
pivoted = pivoted.reset_index()

train = pd.read_csv(folder_path / 'assessment_history_train.csv')  # FIXED
test = pd.read_csv(folder_path / 'assessment_history_test.csv')    # FIXED

train_merged = train.merge(pivoted, on='acct', how='left')
test_merged = test.merge(pivoted, on='acct', how='left')


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2274541461.py:18: DtypeWarning: Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(folder_path + f'building_details_{year}.csv')
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2274541461.py:30: DtypeWarning: Columns (21,23,25,27) have mixed types. Specify dtype option on import or set low_memory=False.
  test = pd.read_csv(folder_path + 'assessment_history_test.csv')


In [ ]:
# Step 1: Identify all '2019' columns in train
train_2019_cols = [col for col in train_merged.columns if '2019' in col]

# Step 2: Find which 2019 columns are missing in test
train_only_2019_cols = [col for col in train_2019_cols if col not in test_merged.columns]

# Step 3: Always drop 'protested_2019' due to leakage risk
train_only_2019_cols.append('protested_2019')

# Step 4: Drop the identified columns from train
train_merged = train_merged.drop(columns=train_only_2019_cols, errors='ignore')

# Step 5: Optional logging
print(f" Dropped {len(train_only_2019_cols)} columns from train (including protested_2019 if present):")
print(train_only_2019_cols)


✅ Dropped 4 columns from train (including protested_2019 if present):
['building_value_2019', 'land_value_2019', 'assessed_2019', 'protested_2019']


In [ ]:
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'protested_2019' in df.columns:
        df.drop(columns='protested_2019', inplace=True)
        print(f" Dropped 'protested_2019' from {df_name}")
    else:
        print(f" 'protested_2019' not found in {df_name}")


ℹ️ 'protested_2019' not found in train_merged
✅ Dropped 'protested_2019' from test_merged


In [ ]:
## Get all '2019' columns in train and test
train_2019_cols = sorted([col for col in train_merged.columns if '2019' in col])
test_2019_cols = sorted([col for col in test_merged.columns if '2019' in col])

# Print train columns
print(" 2019 Columns in train_merged:")
for col in train_2019_cols:
    print(f" - {col}")

print("\n 2019 Columns in test_merged:")
for col in test_2019_cols:
    print(f" - {col}")



📘 2019 Columns in train_merged:
 - bedrooms_2019
 - building_area_2019
 - building_condition_2019
 - deck_area_2019
 - elevator_2019
 - exterior_walls_2019
 - fireplaces_2019
 - floor_area_lower_2019
 - floor_area_primary_2019
 - floor_area_upper_2019
 - floors_2019
 - foundation_type_2019
 - full_bath_2019
 - garage_area_2019
 - grade_2019
 - half_bath_2019
 - has_cooling_2019
 - has_heat_2019
 - land_area_2019
 - mobile_home_area_2019
 - physical_condition_2019
 - porch_area_2019
 - quality_2019
 - quality_description_2019
 - total_rooms_2019
 - year_built_2019
 - year_remodeled_2019

📙 2019 Columns in test_merged:
 - bedrooms_2019
 - building_area_2019
 - building_condition_2019
 - deck_area_2019
 - elevator_2019
 - exterior_walls_2019
 - fireplaces_2019
 - floor_area_lower_2019
 - floor_area_primary_2019
 - floor_area_upper_2019
 - floors_2019
 - foundation_type_2019
 - full_bath_2019
 - garage_area_2019
 - grade_2019
 - half_bath_2019
 - has_cooling_2019
 - has_heat_2019
 - land_a

In [ ]:
# Compare sets
train_only_2019 = sorted(list(set(train_2019_cols) - set(test_2019_cols)))
test_only_2019 = sorted(list(set(test_2019_cols) - set(train_2019_cols)))

# Print comparison result
if not train_only_2019 and not test_only_2019:
    print("\n All 2019 columns match between train_merged and test_merged.")
else:
    print("\n Mismatched 2019 columns found:")

    if train_only_2019:
        print(" In train_merged but not in test_merged:")
        for col in train_only_2019:
            print(f"   - {col}")

    if test_only_2019:
        print(" In test_merged but not in train_merged:")
        for col in test_only_2019:
            print(f"   - {col}")


✅ All 2019 columns match between train_merged and test_merged.


In [6]:
# Step 1: Store target separately
y_train = train_merged["TARGET"].values

# Step 4: Confirm sizes
print(f"Train shape: {train.shape}")
print(f"Test shape: {test.shape}")


Train shape: (628287, 37)
Test shape: (418858, 33)


In [7]:
# Calculate % of missing values in each column of TRAIN only
train_na = (train_merged.isnull().sum() / train_merged.shape[0]) * 100

# Drop columns with no missing values, sort the rest
train_na = train_na[train_na > 0].sort_values(ascending=False)

# Optional: Show top 200 missing features
missing_data = pd.DataFrame({'Missing Ratio (%)': train_na})

# Display
print("Top columns with missing data (based on training set only):")
missing_data.head(20)



Top columns with missing data (based on training set only):


Missing Ratio (%)
building_area_2015                 5.954126
land_value_2015                    5.954126
land_area_2015                     5.954126
protested_2015                     5.954126
assessed_2015                      5.954126
building_value_2015                5.954126
quality_2015                       5.742280
quality_description_2015           5.742280
year_built_2015                    5.742280
year_remodeled_2015                5.742280
building_condition_2015            5.566405
has_cooling_2015                   5.566405
has_heat_2015                      5.566405
physical_condition_2015            5.566405
foundation_type_2015               5.566246
exterior_walls_2015                5.566246
grade_2015                         5.566087
floors_2015                        5.391485
elevator_2015                      5.391485
fireplaces_2015                    5.391485

In [ ]:
def create_floor_area_totals(df, years):
    for y in years:
        primary_col = f'floor_area_primary_{y}'
        upper_col   = f'floor_area_upper_{y}'
        lower_col   = f'floor_area_lower_{y}'
        total_col   = f'floor_area_total_{y}'

        if all(col in df.columns for col in [primary_col, upper_col, lower_col]):
            df[total_col] = (
                df[primary_col].fillna(0) +
                df[upper_col].fillna(0) +
                df[lower_col].fillna(0)
            )
            print(f" Created: {total_col}")
        else:
            print(f" Skipping {total_col} — one or more components missing.")
    return df

# Apply for years 2015–2019
years = ['2015', '2016', '2017', '2018', '2019']
train_merged = create_floor_area_totals(train_merged, years)
test_merged = create_floor_area_totals(test_merged, years)






✅ Created: floor_area_total_2015
✅ Created: floor_area_total_2016
✅ Created: floor_area_total_2017
✅ Created: floor_area_total_2018
✅ Created: floor_area_total_2019
✅ Created: floor_area_total_2015
✅ Created: floor_area_total_2016
✅ Created: floor_area_total_2017
✅ Created: floor_area_total_2018
✅ Created: floor_area_total_2019


In [ ]:
zero_pct = (train_merged['mobile_home_area_2015'] == 0).mean() * 100
print(f" mobile_home_area_2015 is 0 in {zero_pct:.2f}% of training rows")


📊 mobile_home_area_2015 is 0 in 94.42% of training rows


In [ ]:
cols_to_drop = [col for col in train_merged.columns if col.startswith("mobile_home_area")]

# Drop from both sets
train_merged.drop(columns=cols_to_drop, inplace=True, errors='ignore')
test_merged.drop(columns=cols_to_drop, inplace=True, errors='ignore')

print(f" Dropped columns from train/test: {cols_to_drop}")



🗑️ Dropped columns from train/test: ['mobile_home_area_2015', 'mobile_home_area_2016', 'mobile_home_area_2017', 'mobile_home_area_2018', 'mobile_home_area_2019']


In [ ]:
zero_pct = (train_merged['deck_area_2015'] == 0).mean() * 100
print(f" deck_area_2015 is 0 in {zero_pct:.2f}% of training rows")



📊 deck_area_2015 is 0 in 90.66% of training rows


In [ ]:
# Use training columns to identify which deck_area columns exist
cols_to_drop = [col for col in train_merged.columns if col.startswith("deck_area")]

# Drop those columns from both datasets
train_merged.drop(columns=cols_to_drop, inplace=True)
test_merged.drop(columns=cols_to_drop, inplace=True)

print(f" Dropped columns from train/test: {cols_to_drop}")



🗑️ Dropped columns from train/test: ['deck_area_2015', 'deck_area_2016', 'deck_area_2017', 'deck_area_2018', 'deck_area_2019']


In [ ]:
def backfill_yearly_features(df, base_features, years):
    for feature in base_features:
        cols = [f"{feature}_{y}" for y in years if f"{feature}_{y}" in df.columns]
        if len(cols) >= 2:
            # Backfill all relevant year columns in-place
            df[cols] = df[cols].bfill(axis=1)
            print(f" Backfilled: {feature} across {cols}")
        else:
            print(f" Skipping {feature} — not enough year columns found.")
    return df

# Years in reverse so that bfill works from most recent (2019) to oldest (2015)
years = ['2019', '2018', '2017', '2016', '2015']
features = ['garage_area', 'porch_area']

# Apply to both train and test
train_merged = backfill_yearly_features(train_merged, features, years)
test_merged = backfill_yearly_features(test_merged, features, years)



✅ Backfilled: garage_area across ['garage_area_2019', 'garage_area_2018', 'garage_area_2017', 'garage_area_2016', 'garage_area_2015']
✅ Backfilled: porch_area across ['porch_area_2019', 'porch_area_2018', 'porch_area_2017', 'porch_area_2016', 'porch_area_2015']
✅ Backfilled: garage_area across ['garage_area_2019', 'garage_area_2018', 'garage_area_2017', 'garage_area_2016', 'garage_area_2015']
✅ Backfilled: porch_area across ['porch_area_2019', 'porch_area_2018', 'porch_area_2017', 'porch_area_2016', 'porch_area_2015']


In [ ]:
def backfill_yearly_features(df, features, years):
    for feature in features:
        year_cols = [f"{feature}_{y}" for y in years if f"{feature}_{y}" in df.columns]
        if len(year_cols) >= 2:
            df[year_cols] = df[year_cols].bfill(axis=1)
            print(f" Backfilled: {feature} across {year_cols}")
        else:
            print(f" Skipped: Not enough year columns for '{feature}'")
    return df

# Use years in reverse for proper backfill (newest to oldest)
years = ['2019', '2018', '2017', '2016', '2015']
features = ['floors', 'half_bath', 'full_bath', 'total_rooms', 'bedrooms']

# Apply to both train and test
train_merged = backfill_yearly_features(train_merged, features, years)
test_merged = backfill_yearly_features(test_merged, features, years)




✅ Backfilled: floors across ['floors_2019', 'floors_2018', 'floors_2017', 'floors_2016', 'floors_2015']
✅ Backfilled: half_bath across ['half_bath_2019', 'half_bath_2018', 'half_bath_2017', 'half_bath_2016', 'half_bath_2015']
✅ Backfilled: full_bath across ['full_bath_2019', 'full_bath_2018', 'full_bath_2017', 'full_bath_2016', 'full_bath_2015']
✅ Backfilled: total_rooms across ['total_rooms_2019', 'total_rooms_2018', 'total_rooms_2017', 'total_rooms_2016', 'total_rooms_2015']
✅ Backfilled: bedrooms across ['bedrooms_2019', 'bedrooms_2018', 'bedrooms_2017', 'bedrooms_2016', 'bedrooms_2015']
✅ Backfilled: floors across ['floors_2019', 'floors_2018', 'floors_2017', 'floors_2016', 'floors_2015']
✅ Backfilled: half_bath across ['half_bath_2019', 'half_bath_2018', 'half_bath_2017', 'half_bath_2016', 'half_bath_2015']
✅ Backfilled: full_bath across ['full_bath_2019', 'full_bath_2018', 'full_bath_2017', 'full_bath_2016', 'full_bath_2015']
✅ Backfilled: total_rooms across ['total_rooms_2019', 

In [ ]:
# Identify elevator-related columns from training set
elevator_cols = [col for col in train_merged.columns if col.startswith("elevator")]

# Drop from both train and test
train_merged.drop(columns=elevator_cols, inplace=True)
test_merged.drop(columns=elevator_cols, inplace=True)

print(f" Dropped elevator-related columns from train/test: {elevator_cols}")


🗑️ Dropped elevator-related columns from train/test: ['elevator_2015', 'elevator_2016', 'elevator_2017', 'elevator_2018', 'elevator_2019']


In [ ]:
def backfill_year_features(df, features, years):
    for feature in features:
        cols = [f"{feature}_{y}" for y in years if f"{feature}_{y}" in df.columns]
        if len(cols) >= 2:
            df[cols] = df[cols].bfill(axis=1)
            print(f" Backfilled: {feature} across {cols}")
        else:
            print(f" Skipped {feature} — not enough year-based columns found.")
    return df

def create_year_built_final(df):
    year_cols = [f"year_built_{y}" for y in ['2019', '2018', '2017', '2016', '2015'] if f"year_built_{y}" in df.columns]
    if year_cols:
        df['year_built_final'] = df[year_cols].bfill(axis=1).iloc[:, 0]
        print(f" Created year_built_final from: {year_cols}")
    else:
        print(" Skipped: no year_built_* columns found.")
    return df

# Define reverse years for backfill (latest → oldest)
years = ['2019', '2018', '2017', '2016', '2015']
features_to_backfill = ['fireplaces', 'quality', 'quality_description']

# Apply to both train and test
train_merged = backfill_year_features(train_merged, features_to_backfill, years)
train_merged = create_year_built_final(train_merged)

test_merged = backfill_year_features(test_merged, features_to_backfill, years)
test_merged = create_year_built_final(test_merged)



✅ Backfilled: fireplaces across ['fireplaces_2019', 'fireplaces_2018', 'fireplaces_2017', 'fireplaces_2016', 'fireplaces_2015']
✅ Backfilled: quality across ['quality_2019', 'quality_2018', 'quality_2017', 'quality_2016', 'quality_2015']
✅ Backfilled: quality_description across ['quality_description_2019', 'quality_description_2018', 'quality_description_2017', 'quality_description_2016', 'quality_description_2015']
✅ Created year_built_final from: ['year_built_2019', 'year_built_2018', 'year_built_2017', 'year_built_2016', 'year_built_2015']
✅ Backfilled: fireplaces across ['fireplaces_2019', 'fireplaces_2018', 'fireplaces_2017', 'fireplaces_2016', 'fireplaces_2015']
✅ Backfilled: quality across ['quality_2019', 'quality_2018', 'quality_2017', 'quality_2016', 'quality_2015']
✅ Backfilled: quality_description across ['quality_description_2019', 'quality_description_2018', 'quality_description_2017', 'quality_description_2016', 'quality_description_2015']
✅ Created year_built_final from

In [17]:
## Identify columns to drop from training data
cols_to_drop = [col for col in train_merged.columns if col.startswith("year_remodeled")]

# Drop from both train and test
train_merged.drop(columns=cols_to_drop, inplace=True)
test_merged.drop(columns=cols_to_drop, inplace=True)

print(f"🗑️ Dropped year_remodeled-related columns from train/test: {cols_to_drop}")



🗑️ Dropped year_remodeled-related columns from train/test: ['year_remodeled_2015', 'year_remodeled_2016', 'year_remodeled_2017', 'year_remodeled_2018', 'year_remodeled_2019']


In [ ]:
def backfill_categorical_year_features(df, features, years):
    for feature in features:
        year_cols = [f"{feature}_{y}" for y in years if f"{feature}_{y}" in df.columns]
        if len(year_cols) >= 2:
            df[year_cols] = df[year_cols].bfill(axis=1)
            print(f" Backfilled: {feature} across {year_cols}")
        else:
            print(f" Skipped: {feature} — not enough year-based columns.")
    return df

# Backfill from most recent year to oldest
years = ['2019', '2018', '2017', '2016', '2015']
features = ['building_condition', 'foundation_type', 'grade', 'has_cooling', 
            'has_heat', 'physical_condition', 'exterior_walls']

# Apply to train and test
train_merged = backfill_categorical_year_features(train_merged, features, years)
test_merged = backfill_categorical_year_features(test_merged, features, years)




✅ Backfilled: building_condition across ['building_condition_2019', 'building_condition_2018', 'building_condition_2017', 'building_condition_2016', 'building_condition_2015']
✅ Backfilled: foundation_type across ['foundation_type_2019', 'foundation_type_2018', 'foundation_type_2017', 'foundation_type_2016', 'foundation_type_2015']
✅ Backfilled: grade across ['grade_2019', 'grade_2018', 'grade_2017', 'grade_2016', 'grade_2015']
✅ Backfilled: has_cooling across ['has_cooling_2019', 'has_cooling_2018', 'has_cooling_2017', 'has_cooling_2016', 'has_cooling_2015']
✅ Backfilled: has_heat across ['has_heat_2019', 'has_heat_2018', 'has_heat_2017', 'has_heat_2016', 'has_heat_2015']
✅ Backfilled: physical_condition across ['physical_condition_2019', 'physical_condition_2018', 'physical_condition_2017', 'physical_condition_2016', 'physical_condition_2015']
✅ Backfilled: exterior_walls across ['exterior_walls_2019', 'exterior_walls_2018', 'exterior_walls_2017', 'exterior_walls_2016', 'exterior_wal

In [ ]:
def backfill_year_columns(df, features, years):
    for feature in features:
        cols = [f"{feature}_{y}" for y in years if f"{feature}_{y}" in df.columns]
        if len(cols) >= 2:
            df[cols] = df[cols].bfill(axis=1)
            print(f" Backfilled: {feature} across {cols}")
        else:
            print(f" Skipped: {feature} — not enough year-based columns found.")
    return df

# Define year ranges
area_years = ['2019', '2018', '2017', '2016', '2015']
value_years = ['2018', '2017', '2016', '2015']

# Define feature groups
area_features = ['building_area', 'land_area']
value_features = ['building_value', 'land_value', 'assessed']

# Apply to train and test
train_merged = backfill_year_columns(train_merged, area_features, area_years)
train_merged = backfill_year_columns(train_merged, value_features, value_years)

test_merged = backfill_year_columns(test_merged, area_features, area_years)
test_merged = backfill_year_columns(test_merged, value_features, value_years)




✅ Backfilled: building_area across ['building_area_2019', 'building_area_2018', 'building_area_2017', 'building_area_2016', 'building_area_2015']
✅ Backfilled: land_area across ['land_area_2019', 'land_area_2018', 'land_area_2017', 'land_area_2016', 'land_area_2015']
✅ Backfilled: building_value across ['building_value_2018', 'building_value_2017', 'building_value_2016', 'building_value_2015']
✅ Backfilled: land_value across ['land_value_2018', 'land_value_2017', 'land_value_2016', 'land_value_2015']
✅ Backfilled: assessed across ['assessed_2018', 'assessed_2017', 'assessed_2016', 'assessed_2015']
✅ Backfilled: building_area across ['building_area_2019', 'building_area_2018', 'building_area_2017', 'building_area_2016', 'building_area_2015']
✅ Backfilled: land_area across ['land_area_2019', 'land_area_2018', 'land_area_2017', 'land_area_2016', 'land_area_2015']
✅ Backfilled: building_value across ['building_value_2018', 'building_value_2017', 'building_value_2016', 'building_value_2015'

In [ ]:
def backfill_protested_columns(df, years):
    cols = [f"protested_{y}" for y in years if f"protested_{y}" in df.columns]
    if len(cols) >= 2:
        df[cols] = df[cols].bfill(axis=1)
        print(f" Backfilled: protested across {cols}")
    else:
        print(" Skipped protested — not enough year-based columns found.")
    return df

# Only use pre-2019 years to avoid leakage
years = ['2018', '2017', '2016', '2015']

# Apply to both datasets
train_merged = backfill_protested_columns(train_merged, years)
test_merged = backfill_protested_columns(test_merged, years)




✅ Backfilled: protested across ['protested_2018', 'protested_2017', 'protested_2016', 'protested_2015']
✅ Backfilled: protested across ['protested_2018', 'protested_2017', 'protested_2016', 'protested_2015']


In [ ]:
# Save 'acct' from test_merged only
acct_test = test_merged[['acct']].copy() if 'acct' in test_merged.columns else None

# Drop 'acct' from both train and test
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'acct' in df.columns:
        df.drop(columns='acct', inplace=True)
        print(f" Dropped 'acct' from {df_name}")




🗑️ Dropped 'acct' from train_merged
🗑️ Dropped 'acct' from test_merged


In [ ]:
for col in ['zone', 'subneighborhood', 'neighborhood', 'region']:
    if col in train_merged.columns:
        print(f"{col}: {train_merged[col].nunique()} unique values in training set")
    else:
        print(f" {col} not found in training set")


zone: 1589 unique values in training set
subneighborhood: 6161 unique values in training set
neighborhood: 959 unique values in training set
region: 87 unique values in training set


cols_to_drop = ['zone', 'subneighborhood']

for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    drop_cols = [col for col in cols_to_drop if col in df.columns]
    if drop_cols:
        df.drop(columns=drop_cols, inplace=True)
        print(f"🗑️ Dropped columns from {df_name}: {drop_cols}")


In [ ]:
for col in ['neighborhood', 'region','zone','subneighborhood']:
    if col in train_merged.columns:
        # Step 1: Compute frequency from training data
        freq_map = train_merged[col].value_counts(normalize=True)

        # Step 2: Apply to both datasets
        train_merged[f'{col}_freq'] = train_merged[col].map(freq_map)
        test_merged[f'{col}_freq'] = test_merged[col].map(freq_map)

        print(f" Frequency encoded: {col} → {col}_freq (based on training set)")
    else:
        print(f" Column '{col}' not found in training set")


✅ Frequency encoded: neighborhood → neighborhood_freq (based on training set)


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_merged[f'{col}_freq'] = train_merged[col].map(freq_map)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_merged[f'{col}_freq'] = test_merged[col].map(freq_map)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the resu

✅ Frequency encoded: region → region_freq (based on training set)
✅ Frequency encoded: zone → zone_freq (based on training set)


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_merged[f'{col}_freq'] = train_merged[col].map(freq_map)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_merged[f'{col}_freq'] = test_merged[col].map(freq_map)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the resu

✅ Frequency encoded: subneighborhood → subneighborhood_freq (based on training set)


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2858503920.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_merged[f'{col}_freq'] = test_merged[col].map(freq_map)


In [ ]:
if all(col in train_merged.columns for col in ['land_area_2019', 'land_area_2015']):
    growth = train_merged['land_area_2019'] - train_merged['land_area_2015']
    changed_pct = (growth != 0).mean() * 100
    print(f" Percentage of homes with land area change (2015→2019): {changed_pct:.2f}%")
else:
    print(" One or both columns ('land_area_2015', 'land_area_2019') not found in training set")




🧪 Percentage of homes with land area change (2015→2019): 6.42%


In [ ]:
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'year_built_final' in df.columns:
        df['year_built_final'] = df['year_built_final'].astype(str)
        print(f" Converted 'year_built_final' to string in {df_name}")
    else:
        print(f" 'year_built_final' not found in {df_name}")


🔤 Converted 'year_built_final' to string in train_merged
🔤 Converted 'year_built_final' to string in test_merged


In [ ]:
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'floor_area_total_final' in df.columns and 'year_built_final' in df.columns:
        df.loc[df['floor_area_total_final'] == 0, 'year_built_final'] = 'None'
        print(f" Set 'year_built_final' to 'None' where 'floor_area_total_final' == 0 in {df_name}")
    else:
        print(f" Required columns missing in {df_name}")


⚠️ Required columns missing in train_merged
⚠️ Required columns missing in test_merged


In [ ]:
# Define year ranges per feature type
value_years = range(2015, 2019)   # 2015–2018 for value columns
area_years  = range(2015, 2020)   # 2015–2019 for area columns

# Define base columns
base_cols_year_map = {
    'building_value': value_years,
    'land_value': value_years,
    'building_area': area_years,
    'land_area': area_years,
}

# Generate full list of columns to impute
cols_to_impute = []
for base, years in base_cols_year_map.items():
    for year in years:
        cols_to_impute.append(f"{base}_{year}")

# Impute using neighborhood → region strategy
for col in cols_to_impute:
    # First, fill by neighborhood (train only)
    if 'neighborhood' in train_merged.columns:
        medians_by_neigh = train_merged.groupby('neighborhood')[col].median()
        train_merged[col] = train_merged.apply(
            lambda row: medians_by_neigh[row['neighborhood']] if pd.isna(row[col]) else row[col], axis=1)
        test_merged[col] = test_merged.apply(
            lambda row: medians_by_neigh.get(row['neighborhood'], np.nan) if pd.isna(row[col]) else row[col], axis=1)

    # Then, fill remaining by region (train only)
    if 'region' in train_merged.columns:
        medians_by_region = train_merged.groupby('region')[col].median()
        train_merged[col] = train_merged.apply(
            lambda row: medians_by_region[row['region']] if pd.isna(row[col]) else row[col], axis=1)
        test_merged[col] = test_merged.apply(
            lambda row: medians_by_region.get(row['region'], np.nan) if pd.isna(row[col]) else row[col], axis=1)

    print(f" Imputed '{col}' using group medians (neighborhood → region) from training data")



✅ Imputed 'building_value_2015' using group medians (neighborhood → region) from training data
✅ Imputed 'building_value_2016' using group medians (neighborhood → region) from training data
✅ Imputed 'building_value_2017' using group medians (neighborhood → region) from training data
✅ Imputed 'building_value_2018' using group medians (neighborhood → region) from training data
✅ Imputed 'land_value_2015' using group medians (neighborhood → region) from training data
✅ Imputed 'land_value_2016' using group medians (neighborhood → region) from training data
✅ Imputed 'land_value_2017' using group medians (neighborhood → region) from training data
✅ Imputed 'land_value_2018' using group medians (neighborhood → region) from training data
✅ Imputed 'building_area_2015' using group medians (neighborhood → region) from training data
✅ Imputed 'building_area_2016' using group medians (neighborhood → region) from training data
✅ Imputed 'building_area_2017' using group medians (neighborhood → r

In [ ]:
from pandas.api.types import is_numeric_dtype

# Step 1: Coerce non-numeric to NaN in both sets
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'year_built_final' in df.columns:
        df['year_built_final'] = pd.to_numeric(df['year_built_final'], errors='coerce')
        print(f" Coerced 'year_built_final' to numeric in {df_name}")

# Step 2: Group-based imputation (use training data only)
if 'year_built_final' in train_merged.columns and 'neighborhood' in train_merged.columns:
    # Neighborhood-based median from train
    neigh_medians = train_merged.groupby('neighborhood')['year_built_final'].median()

    # Apply to train
    train_merged['year_built_final'] = train_merged.apply(
        lambda row: neigh_medians[row['neighborhood']] if pd.isna(row['year_built_final']) else row['year_built_final'], axis=1)

    # Apply to test
    test_merged['year_built_final'] = test_merged.apply(
        lambda row: neigh_medians.get(row['neighborhood'], np.nan) if pd.isna(row['year_built_final']) else row['year_built_final'], axis=1)

if 'region' in train_merged.columns:
    # Region-based fallback median from train
    region_medians = train_merged.groupby('region')['year_built_final'].median()

    train_merged['year_built_final'] = train_merged.apply(
        lambda row: region_medians[row['region']] if pd.isna(row['year_built_final']) else row['year_built_final'], axis=1)

    test_merged['year_built_final'] = test_merged.apply(
        lambda row: region_medians.get(row['region'], np.nan) if pd.isna(row['year_built_final']) else row['year_built_final'], axis=1)

print(" Imputed 'year_built_final' using neighborhood → region medians from training set")


🔢 Coerced 'year_built_final' to numeric in train_merged
🔢 Coerced 'year_built_final' to numeric in test_merged
✅ Imputed 'year_built_final' using neighborhood → region medians from training set


In [ ]:
# List of all assessed columns to impute
assessed_cols = ['assessed_2015', 'assessed_2016', 'assessed_2017', 'assessed_2018']

for col in assessed_cols:
    if col not in train_merged.columns:
        continue

    # Step 1: Compute medians from training data only
    neigh_medians = train_merged.groupby('neighborhood')[col].median()
    region_medians = train_merged.groupby('region')[col].median()
    global_median = train_merged[col].median()

    # Step 2: Train set imputation
    train_merged[col] = train_merged.apply(
        lambda row: neigh_medians[row['neighborhood']]
        if pd.isna(row[col]) and row['neighborhood'] in neigh_medians else
        region_medians[row['region']]
        if pd.isna(row[col]) and row['region'] in region_medians else
        global_median
        if pd.isna(row[col]) else
        row[col],
        axis=1
    )

    # Step 3: Test set imputation (using train medians only)
    test_merged[col] = test_merged.apply(
        lambda row: neigh_medians.get(row['neighborhood'], np.nan)
        if pd.isna(row[col]) else row[col],
        axis=1
    )
    test_merged[col] = test_merged.apply(
        lambda row: region_medians.get(row['region'], np.nan)
        if pd.isna(row[col]) else row[col],
        axis=1
    )
    test_merged[col].fillna(global_median, inplace=True)

    print(f" Imputed '{col}' using neighborhood → region → global medians (from training data)")


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1220954033.py:36: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  test_merged[col].fillna(global_median, inplace=True)


✅ Imputed 'assessed_2015' using neighborhood → region → global medians (from training data)


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1220954033.py:36: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  test_merged[col].fillna(global_median, inplace=True)


✅ Imputed 'assessed_2016' using neighborhood → region → global medians (from training data)


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1220954033.py:36: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  test_merged[col].fillna(global_median, inplace=True)


✅ Imputed 'assessed_2017' using neighborhood → region → global medians (from training data)
✅ Imputed 'assessed_2018' using neighborhood → region → global medians (from training data)


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1220954033.py:36: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  test_merged[col].fillna(global_median, inplace=True)


In [ ]:
# === Step 1: Compute neighborhood-level stats ===
neigh_stats = train_merged.groupby('neighborhood')['assessed_2018'].agg([
    ('neigh_assess_mean', 'mean'),
    ('neigh_assess_median', 'median'),
    ('neigh_assess_std', 'std'),
    ('neigh_assess_q1', lambda x: x.quantile(0.25)),
    ('neigh_assess_q3', lambda x: x.quantile(0.75)),
]).reset_index()
neigh_stats['neigh_assess_iqr'] = neigh_stats['neigh_assess_q3'] - neigh_stats['neigh_assess_q1']

# === Step 2: Compute region-level stats ===
region_stats = train_merged.groupby('region')['assessed_2018'].agg([
    ('region_assess_mean', 'mean'),
    ('region_assess_median', 'median'),
    ('region_assess_std', 'std'),
    ('region_assess_q1', lambda x: x.quantile(0.25)),
    ('region_assess_q3', lambda x: x.quantile(0.75)),
]).reset_index()
region_stats['region_assess_iqr'] = region_stats['region_assess_q3'] - region_stats['region_assess_q1']

# === Step 3: Fallback std maps from training data ===
# For neighborhood fallback, group region medians of neighborhood std
neigh_std_by_region = neigh_stats.merge(train_merged[['neighborhood', 'region']], on='neighborhood', how='left') \
                                  .groupby('region')['neigh_assess_std'].median()
global_neigh_std = neigh_stats['neigh_assess_std'].median()

region_std_by_neigh = region_stats.merge(train_merged[['neighborhood', 'region']], on='region', how='left') \
                                   .groupby('neighborhood')['region_assess_std'].median()
global_region_std = region_stats['region_assess_std'].median()

# === Step 4: Merge into train/test and compute features ===
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    df = df.merge(neigh_stats, on='neighborhood', how='left')
    df = df.merge(region_stats, on='region', how='left')

    # Fill missing std values via fallback
    df['neigh_assess_std'] = df['neigh_assess_std'].fillna(
        df['region'].map(neigh_std_by_region)
    ).fillna(global_neigh_std)

    df['region_assess_std'] = df['region_assess_std'].fillna(
        df['neighborhood'].map(region_std_by_neigh)
    ).fillna(global_region_std)

    # Compute derived features
    df['assess_minus_neigh_mean'] = df['assessed_2018'] - df['neigh_assess_mean']
    df['assess_ratio_neigh_mean'] = df['assessed_2018'] / (df['neigh_assess_mean'] + 1e-6)
    df['z_score_assess_neigh'] = df['assess_minus_neigh_mean'] / (df['neigh_assess_std'] + 1e-6)

    df['assess_minus_region_mean'] = df['assessed_2018'] - df['region_assess_mean']
    df['assess_ratio_region_mean'] = df['assessed_2018'] / (df['region_assess_mean'] + 1e-6)
    df['z_score_assess_region'] = df['assess_minus_region_mean'] / (df['region_assess_std'] + 1e-6)

    # Save back
    if df_name == 'train_merged':
        train_merged = df
    else:
        test_merged = df

print(" Completed: Stats merge + std fallback + z-score computation.")


✅ Completed: Stats merge + std fallback + z-score computation.


In [ ]:
cols_to_drop = ['neighborhood', 'region','zone','subneighborhood']

for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    drop_cols = [col for col in cols_to_drop if col in df.columns]
    if drop_cols:
        df.drop(columns=drop_cols, inplace=True)
        print(f" Dropped columns from {df_name}: {drop_cols}")


🗑️ Dropped columns from train_merged: ['neighborhood', 'region', 'zone', 'subneighborhood']
🗑️ Dropped columns from test_merged: ['neighborhood', 'region', 'zone', 'subneighborhood']


In [ ]:
growth_pairs = {
    'building_value_growth': ('building_value_2018', 'building_value_2015'),
    'land_value_growth':     ('land_value_2018', 'land_value_2015'),
    'assessed_growth':       ('assessed_2018', 'assessed_2015')
}

for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    for new_col, (final_col, base_col) in growth_pairs.items():
        if final_col in df.columns and base_col in df.columns:
            df[new_col] = df[final_col] - df[base_col]
            print(f" Created {new_col} in {df_name}")
        else:
            print(f" Skipped {new_col} in {df_name}: missing {final_col} or {base_col}")

    # === Building Age ===
    if 'year_built_final' in df.columns:
        df['year_built_final'] = pd.to_numeric(df['year_built_final'], errors='coerce')  # handle 'Vacant', etc.
        df['building_age'] = 2018 - df['year_built_final']
        print(f" Created building_age in {df_name}")
    else:
        print(f" Skipped building_age in {df_name}: missing year_built_final")


✅ Created building_value_growth in train_merged
✅ Created land_value_growth in train_merged
✅ Created assessed_growth in train_merged
✅ Created building_age in train_merged
✅ Created building_value_growth in test_merged
✅ Created land_value_growth in test_merged
✅ Created assessed_growth in test_merged
✅ Created building_age in test_merged


In [ ]:
if 'school_dist' in train_merged.columns:
    missing_pct = train_merged['school_dist'].isna().mean() * 100
    missing_count = train_merged['school_dist'].isna().sum()

    print(f" 'school_dist' has {missing_count} missing values ({missing_pct:.2f}%) in training set")
else:
    print(" 'school_dist' not found in training set")


🔍 'school_dist' has 3 missing values (0.00%) in training set


In [ ]:
if 'school_dist' in train_merged.columns:
    school_dist_median = train_merged['school_dist'].median()

    for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
        if 'school_dist' in df.columns:
            df['school_dist'] = df['school_dist'].fillna(school_dist_median)
            print(f" Filled missing 'school_dist' in {df_name} using train median ({school_dist_median})")
else:
    print(" 'school_dist' not found in train_merged")


✅ Filled missing 'school_dist' in train_merged using train median (8.0)
✅ Filled missing 'school_dist' in test_merged using train median (8.0)


In [ ]:
if 'year_built_final' in train_merged.columns:
    missing_pct = train_merged['year_built_final'].isna().mean() * 100
    missing_count = train_merged['year_built_final'].isna().sum()

    print(f" 'year_built_final' has {missing_count} missing values ({missing_pct:.2f}%) in training set")
else:
    print(" 'year_built_final' not found in training set")


🔍 'year_built_final' has 0 missing values (0.00%) in training set


In [ ]:
# === STEP 0: Define base feature names ===
numeric_bases = [
    'garage_area', 'porch_area', 'floors', 'half_bath', 'full_bath',
    'total_rooms', 'bedrooms', 'fireplaces', 'building_area', 'building_value'
]

categorical_fill_map = {
    'quality': 'None',
    'quality_description': 'None',
    'building_condition': 'None',
    'foundation_type': 'None',
    'grade': 'None',
    'has_cooling': False,
    'has_heat': False,
    'physical_condition': 'None',
    'exterior_walls': 'None',
    'protested': False
}

# Generate full list of columns (2015–2019 only, no final columns)
numeric_cols_to_zero = [
    f'{base}_{year}' for base in numeric_bases for year in range(2015, 2020)
] + ['building_value_growth']

categorical_cols_to_fill = {
    f'{base}_{year}': val
    for base, val in categorical_fill_map.items()
    for year in range(2015, 2020)
}

# === STEP 1: Apply imputation if floor_area_total_2019 == 0 ===
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'floor_area_total_2019' in df.columns:
        zero_floor_mask = df['floor_area_total_2019'] == 0

        # Fill numeric columns with 0
        for col in numeric_cols_to_zero:
            if col in df.columns:
                df.loc[zero_floor_mask, col] = df.loc[zero_floor_mask, col].fillna(0)

        # Fill categorical/boolean columns
        for col, fill_val in categorical_cols_to_fill.items():
            if col in df.columns:
                df.loc[zero_floor_mask, col] = df.loc[zero_floor_mask, col].fillna(fill_val)

        print(f" Filled structure-dependent missing values in {df_name} for {zero_floor_mask.sum()} rows")
    else:
        print(f" 'floor_area_total_2019' not found in {df_name}")



/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1001132961.py:44: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df.loc[zero_floor_mask, col] = df.loc[zero_floor_mask, col].fillna(fill_val)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1001132961.py:44: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df.loc[zero_floor_mask, col] = df.loc[zero_floor_mask, col].fillna(fill_val)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1001132961.py:44: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .

✅ Filled structure-dependent missing values in train_merged for 218 rows
✅ Filled structure-dependent missing values in test_merged for 150 rows


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1001132961.py:44: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df.loc[zero_floor_mask, col] = df.loc[zero_floor_mask, col].fillna(fill_val)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1001132961.py:44: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df.loc[zero_floor_mask, col] = df.loc[zero_floor_mask, col].fillna(fill_val)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1001132961.py:44: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .

In [37]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import OrdinalEncoder
from sklearn.model_selection import KFold

# Clear specific variables
for var in ['ordinal_cols_all', 'bool_cols_all']:
    if var in locals():
        del globals()[var]

# === STEP 1: Boolean Encoding (2015–2019 only) ===
bool_bases = ['has_cooling', 'has_heat', 'protested']
bool_cols_all = [f"{base}_{year}" for base in bool_bases for year in range(2015, 2020)]

for col in bool_cols_all:
    if col in train_merged.columns:
        mode_val = train_merged[col].mode(dropna=True)[0]
        train_merged[col] = train_merged[col].fillna(mode_val).astype(int)
        test_merged[col] = test_merged[col].fillna(mode_val).astype(int)

# === STEP 2: Ordinal Cleaning and Encoding (2015–2019 only) ===
ordinal_bases = [
    'quality', 'quality_description', 'grade',
    'building_condition', 'physical_condition'
]

ordinal_cols_all = [f"{base}_{year}" for base in ordinal_bases for year in range(2015, 2020)]

# Column-specific replacements
replacement_maps = {
    'quality': {'E': 'D', 'F': 'D', 'X': np.nan, 'None': np.nan},
    'quality_description': {'Poor': 'Very Low', 'None': np.nan},
    'grade': {'X': 'F', 'X-': 'F', 'X+': 'F', 'E': 'D', 'E-': 'D-', 'E+': 'D+', 'None': np.nan},
    'building_condition': {'Very Poor': 'Poor', 'Unsound': 'Poor', 'None': np.nan},
    'physical_condition': {'Very Poor': 'Poor', 'Unsound': 'Poor', 'None': np.nan}
}

# Ordinal category order
ord_categories = {
    'quality': ['D', 'C', 'B', 'A'],
    'quality_description': ['Very Low', 'Low', 'Average', 'Good', 'Excellent', 'Superior'],
    'grade': ['F', 'D-', 'D', 'D+', 'C-', 'C', 'C+', 'B-', 'B', 'B+', 'A-', 'A', 'A+'],
    'building_condition': ['Poor', 'Fair', 'Average', 'Good', 'Very Good', 'Excellent'],
    'physical_condition': ['Poor', 'Fair', 'Average', 'Good', 'Very Good', 'Excellent']
}

# Clean and encode
for base in ordinal_bases:
    for year in range(2015, 2020):
        col = f"{base}_{year}"
        if col in train_merged.columns:
            replacements = replacement_maps.get(base, {})
            train_merged[col] = train_merged[col].replace(replacements)
            test_merged[col] = test_merged[col].replace(replacements)

            mode_val = train_merged[col].mode(dropna=True)[0]
            train_merged[col] = train_merged[col].fillna(mode_val)
            test_merged[col] = test_merged[col].fillna(mode_val)

            encoder = OrdinalEncoder(categories=[ord_categories[base]], handle_unknown='use_encoded_value', unknown_value=-1)
            train_merged[[col]] = encoder.fit_transform(train_merged[[col]])
            test_merged[[col]] = encoder.transform(test_merged[[col]])



/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2484106990.py:18: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  train_merged[col] = train_merged[col].fillna(mode_val).astype(int)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2484106990.py:19: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  test_merged[col] = test_merged[col].fillna(mode_val).astype(int)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/2484106990.py:18: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated an

In [ ]:
# === STEP 3: Target Encoding (2015–2019 only) ===
def group_and_target_encode_cv(train_df, test_df, target_name, column, rare_threshold=0.001, smoothing=10, n_splits=5):
    freq = train_df[column].value_counts(normalize=True)
    rare_cats = freq[freq < rare_threshold].index
    train_df[column] = train_df[column].replace(rare_cats, 'Other')
    test_df[column] = test_df[column].replace(rare_cats, 'Other')

    global_mean = train_df[target_name].mean()
    oof_encoded = pd.Series(index=train_df.index, dtype='float64')

    kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)
    for train_idx, val_idx in kf.split(train_df):
        X_tr, X_val = train_df.iloc[train_idx], train_df.iloc[val_idx]
        stats = X_tr.groupby(column)[target_name].agg(['mean', 'count'])
        smooth = (stats['mean'] * stats['count'] + global_mean * smoothing) / (stats['count'] + smoothing)
        oof_encoded.iloc[val_idx] = X_val[column].map(smooth).fillna(global_mean)

    final_stats = train_df.groupby(column)[target_name].agg(['mean', 'count'])
    final_smooth = (final_stats['mean'] * final_stats['count'] + global_mean * smoothing) / (final_stats['count'] + smoothing)
    test_encoded = test_df[column].map(final_smooth).fillna(global_mean)

    return oof_encoded, test_encoded

# Target-encodable nominal columns
target_encodable_bases = ['foundation_type', 'exterior_walls']
target_encodable_cols_all = [f"{base}_{year}" for base in target_encodable_bases for year in range(2015, 2020)]

# Apply target encoding
for col in target_encodable_cols_all:
    if col in train_merged.columns:
        mode_val = train_merged[col].mode(dropna=True)[0]
        train_merged[col] = train_merged[col].fillna(mode_val)
        test_merged[col] = test_merged[col].fillna(mode_val)

        train_merged[f'{col}_te'], test_merged[f'{col}_te'] = group_and_target_encode_cv(
            train_merged, test_merged, target_name='assessed_2018', column=col,
            rare_threshold=0.001, smoothing=10, n_splits=5
        )

        train_merged.drop(columns=[col], inplace=True)
        test_merged.drop(columns=[col], inplace=True)

print(" Done: Boolean, Ordinal, and Target Encoding for 2015–2019 features only.")

✅ Done: Boolean, Ordinal, and Target Encoding for 2015–2019 features only.


In [ ]:
# Step 1: Get growth columns from training set
growth_cols = [col for col in train_merged.columns if '_growth' in col]

# Step 2: Compute medians from train_merged only
growth_medians = {col: train_merged[col].median() for col in growth_cols}

# Step 3: Apply to both train and test
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    for col in growth_cols:
        if col in df.columns:
            df[f'{col}_missing'] = df[col].isna().astype(int)
            df[col].fillna(growth_medians[col], inplace=True)
    print(f" Filled and flagged missing values in {df_name} for: {growth_cols}")


✅ Filled and flagged missing values in train_merged for: ['building_value_growth', 'land_value_growth', 'assessed_growth']
✅ Filled and flagged missing values in test_merged for: ['building_value_growth', 'land_value_growth', 'assessed_growth']


/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1664657720.py:12: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df[col].fillna(growth_medians[col], inplace=True)
/var/folders/sl/hc9dmfps60l7lq3bh_fp8ny40000gn/T/ipykernel_3001/1664657720.py:12: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values alw

In [ ]:

# === Step 1: List your growth features ===
growth_features = ['land_value_growth', 'building_value_growth', 'assessed_growth']

# === Step 2: Binning Function (train-based binning) ===
def bin_growth_feature_safe(train_df, test_df, feature, bins=4):
    try:
        # Quantile binning on train only
        train_df[f'{feature}_bin'], bin_edges = pd.qcut(train_df[feature], q=bins, labels=False, retbins=True, duplicates='drop')
        test_df[f'{feature}_bin'] = pd.cut(test_df[feature], bins=bin_edges, labels=False, include_lowest=True)
    except ValueError:
        # Fallback: Equal-width binning
        min_val = train_df[feature].min()
        max_val = train_df[feature].max()
        bin_edges = np.linspace(min_val, max_val, bins + 1)
        train_df[f'{feature}_bin'] = pd.cut(train_df[feature], bins=bin_edges, labels=False, include_lowest=True)
        test_df[f'{feature}_bin'] = pd.cut(test_df[feature], bins=bin_edges, labels=False, include_lowest=True)

    # Convert to category
    train_df[f'{feature}_bin'] = train_df[f'{feature}_bin'].astype('category')
    test_df[f'{feature}_bin'] = test_df[f'{feature}_bin'].astype('category')
    return train_df, test_df

# === Step 3: Apply to train_merged and test_merged ===
for feature in growth_features:
    train_merged, test_merged = bin_growth_feature_safe(train_merged, test_merged, feature)

# === Step 4: Bin year_built_final using train-based quantiles ===
train_merged['year_built_bin'], bin_edges = pd.qcut(
    train_merged['year_built_final'], q=5, retbins=True, labels=False, duplicates='drop'
)
test_merged['year_built_bin'] = pd.cut(
    test_merged['year_built_final'], bins=bin_edges, labels=False, include_lowest=True
)

# Convert to category
train_merged['year_built_bin'] = train_merged['year_built_bin'].astype('category')
test_merged['year_built_bin'] = test_merged['year_built_bin'].astype('category')


print(" Binned growth & year_built features safely with no leakage.")



✅ Binned growth & year_built features safely with no leakage.


In [41]:
# === Step 5: Drop original continuous columns ===
cols_to_drop = growth_features + ['year_built_final']
train_merged=train_merged.drop(columns=cols_to_drop)
test_merged=test_merged.drop(columns=cols_to_drop)

In [ ]:
rare_threshold = 0.001  # 0.1%

cat_cols = [
    "quality_description_final",
    "foundation_type_final_te",
    "physical_condition_final",
    "exterior_walls_final_te",
    "region_freq",
    "neighborhood_freq"
]

for col in cat_cols:
    if col in train_merged.columns:
        freq = train_merged[col].value_counts(normalize=True)
        rare = freq[freq < rare_threshold]
        if not rare.empty:
            print(f"\n Rare categories in '{col}' (less than 0.1% of training data):\n{rare}")
    else:
        print(f" Column '{col}' not found in train_merged")




⚠️ Column 'quality_description_final' not found in train_merged
⚠️ Column 'foundation_type_final_te' not found in train_merged
⚠️ Column 'physical_condition_final' not found in train_merged
⚠️ Column 'exterior_walls_final_te' not found in train_merged

⚠️ Rare categories in 'region_freq' (less than 0.1% of training data):
region_freq
0.000963    0.000963
0.000641    0.000641
0.000347    0.000347
0.000159    0.000159
0.000083    0.000083
0.000010    0.000019
0.000002    0.000019
0.000008    0.000016
0.000005    0.000005
Name: proportion, dtype: float64

⚠️ Rare categories in 'neighborhood_freq' (less than 0.1% of training data):
neighborhood_freq
0.000500    0.001000
0.000996    0.000996
0.000988    0.000988
0.000984    0.000984
0.000492    0.000984
              ...   
0.000008    0.000024
0.000021    0.000021
0.000014    0.000014
0.000002    0.000006
0.000003    0.000006
Name: proportion, Length: 321, dtype: float64


In [ ]:
# Define frequency columns and threshold
freq_cols = ['region_freq', 'neighborhood_freq', 'zone_freq', 'subneighborhood_freq']
rare_thresh = 0.001

# Apply rare value replacement for each frequency column
for col in freq_cols:
    if col in train_merged.columns:
        rare_vals = train_merged[col].value_counts(normalize=True)[lambda x: x < rare_thresh].index
        train_merged[col] = train_merged[col].replace(rare_vals, 0)
        test_merged[col] = test_merged[col].replace(rare_vals, 0)
        print(f" Replaced rare values in {col} using train_merged threshold < {rare_thresh}")
    else:
        print(f" Column {col} not found in train_merged — skipping.")



✅ Replaced rare values in region_freq using train_merged threshold < 0.001
✅ Replaced rare values in neighborhood_freq using train_merged threshold < 0.001
✅ Replaced rare values in zone_freq using train_merged threshold < 0.001
✅ Replaced rare values in subneighborhood_freq using train_merged threshold < 0.001


In [ ]:
import pandas as pd

# === Compute skewness for numeric columns ===
numeric_cols = train_merged.select_dtypes(include=[np.number])
skew_values = numeric_cols.skew().sort_values(ascending=False)

# === Save skewness to CSV ===
skew_df = skew_values.reset_index()
skew_df.columns = ['feature', 'skewness']
skew_df.to_csv("feature_skewness.csv", index=False)

print(" Saved skewness stats to 'feature_skewness.csv'")


📁 Saved skewness stats to 'feature_skewness.csv'


In [ ]:
import pandas as pd

# Load your skewness report
skew_df = pd.read_csv("feature_skewness.csv")  # Update path if needed

# === Step 1: Categorize features by skew level ===
ultra_skewed = []
moderately_skewed = []

for _, row in skew_df.iterrows():
    feature = row['feature']
    skew = row['skewness']
    
    if feature not in train_merged.columns:
        continue

    unique_vals = train_merged[feature].nunique()
    is_binary = set(train_merged[feature].dropna().unique()).issubset({0, 1})

    if unique_vals > 10 and not is_binary and not feature.endswith('_te'):
        if skew > 100:
            ultra_skewed.append(feature)
        elif 2< skew <= 100:
            moderately_skewed.append(feature)

print(f" {len(ultra_skewed)} ultra-skewed features to clip at 0.995.")
print(f" {len(moderately_skewed)} moderately-skewed features to clip at 0.999.")

# === Step 2: Compute quantile clipping bounds ===
clip_bounds = {}

for col in ultra_skewed:
    clip_bounds[col] = (
        train_merged[col].quantile(0.005),
        train_merged[col].quantile(0.995)
    )

for col in moderately_skewed:
    clip_bounds[col] = (
        train_merged[col].quantile(0.001),
        train_merged[col].quantile(0.999)
    )

# === Step 3: Apply clipping to both train and test ===
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    for col, (lower, upper) in clip_bounds.items():
        if col in df.columns:
            df[col] = df[col].clip(lower, upper)

print(" Adaptive clipping applied: 0.995 for ultra-skewed, 0.999 for moderately-skewed features.")


✅ 5 ultra-skewed features to clip at 0.995.
✅ 76 moderately-skewed features to clip at 0.999.
✂️ Adaptive clipping applied: 0.995 for ultra-skewed, 0.999 for moderately-skewed features.


In [46]:
def add_features(df):
    df = df.copy()
    
    # === Ratio features ===
    df['area_ratio'] = df['building_area_2019'] / (df['land_area_2019'] + 1)
    df['porch_ratio'] = df['porch_area_2019'] / (df['building_area_2019'] + 1)
    df['floor_density'] = df['floor_area_total_2019'] / (df['land_area_2019'] + 1)
    
    df['value_ratio'] = df['building_value_2018'] / (df['land_value_2018'] + 1)
    df['value_per_sqft'] = df['building_value_2018'] / (df['building_area_2019'] + 1)
    df['price_per_sqft'] = df['assessed_2018'] / (df['building_area_2019'] + 1)

    # === Bathroom & room structure ===
    df['bathroom_score'] = df['full_bath_2019'] + 0.5 * df['half_bath_2019']
    df['bathroom_density'] = df['bathroom_score'] / (df['total_rooms_2019'] + 1)
    df['bedroom_ratio'] = df['bedrooms_2019'] / (df['total_rooms_2019'] + 1)
    df['rooms_per_floor'] = df['total_rooms_2019'] / (df['floors_2019'] + 1)

    # === Core interactions ===
    df['bedrooms_x_floors'] = df['bedrooms_2019'] * df['floors_2019']
    df['rooms_x_quality'] = df['total_rooms_2019'] * df['quality_2019']
    df['assess_x_age'] = df['assessed_2018'] * df['building_age']
    df['grade_quality_index'] = df['grade_2019'] * df['quality_2019']

    # === Selected high-signal interactions ===
    df['area_x_quality'] = df['building_area_2019'] * df['quality_2019']
    df['floor_area_x_grade'] = df['floor_area_total_2019'] * df['grade_2019']
    df['value_to_neigh_median'] = df['building_value_2018'] / (df['neigh_assess_median'] + 1)
    df['assess_to_neigh_mean'] = df['assessed_2018'] / (df['neigh_assess_mean'] + 1)
    df['value_per_age'] = df['building_value_2018'] / (df['building_age'] + 1)

    # === Clean up ===
    df = df.replace([np.inf, -np.inf], np.nan)
    df = df.fillna(0)
    
    return df

# === Apply to train and test sets ===
train_merged = add_features(train_merged)
test_merged = add_features(test_merged)



In [47]:
# Select numeric columns only
numeric_features = train_merged.select_dtypes(include=['int64', 'float64'])

# Calculate skewness
skewness = numeric_features.skew(numeric_only=True)

# Filter and sort features with skewness > 30
highly_skewed = skewness[skewness > 5].sort_values(ascending=False)

print("📊 Features with skewness > 5:")
print(highly_skewed)

📊 Features with skewness > 5:
building_value_growth_missing    354.478490
land_value_growth_missing        354.478490
assessed_growth_missing           33.631805
value_ratio                       22.718640
foundation_type_2017_te           19.398895
foundation_type_2018_te           19.209417
foundation_type_2016_te           19.088215
foundation_type_2019_te           18.622057
foundation_type_2015_te           17.140939
floor_density                     14.857656
area_ratio                        14.266433
floor_area_lower_2015              9.470069
floor_area_lower_2016              9.001662
assess_x_age                       8.945820
floor_area_lower_2017              8.676705
neigh_assess_std                   8.407189
floor_area_lower_2018              8.338474
floor_area_lower_2019              7.911224
neigh_assess_iqr                   6.953338
value_per_age                      6.361554
land_area_2019                     6.145570
land_area_2018                     6.130493
la

In [ ]:
import numpy as np
import pandas as pd

# === Step 1: Drop dummy _missing columns ===
drop_cols = [
    'building_value_growth_missing',
    'land_value_growth_missing',
    'assessed_growth_missing'
]
train_merged = train_merged.drop(columns=drop_cols, errors='ignore')
test_merged = test_merged.drop(columns=drop_cols, errors='ignore')
print("🗑️ Dropped dummy _missing columns from train and test.")

# === Step 2: Compute skewness from train_merged only ===
numeric_cols = train_merged.select_dtypes(include=[np.number])
skew_series = numeric_cols.skew()

# === Step 3: Categorize by skew level (excluding _te and _missing) ===
ultra_skewed = []
moderately_skewed = []

for col, skew_val in skew_series.items():
    if col.endswith('_te') or col.endswith('_missing'):
        continue
    if skew_val > 100:
        ultra_skewed.append(col)
    elif skew_val > 2:
        moderately_skewed.append(col)

print(f" {len(ultra_skewed)} ultra-skewed features (clip at 0.5%–99.5%).")
print(f" {len(moderately_skewed)} moderately-skewed features (clip at 0.1%–99.9%).")

# === Step 4: Compute clipping bounds ===
clip_bounds = {}

for col in ultra_skewed:
    clip_bounds[col] = (
        train_merged[col].quantile(0.005),
        train_merged[col].quantile(0.995)
    )

for col in moderately_skewed:
    clip_bounds[col] = (
        train_merged[col].quantile(0.001),
        train_merged[col].quantile(0.999)
    )

# === Step 5: Apply clipping to both train and test sets ===
for df in [train_merged, test_merged]:
    for col, (lower, upper) in clip_bounds.items():
        if col in df.columns:
            df[col] = df[col].clip(lower, upper)

print(" Adaptive clipping complete: 0.995 for ultra-skewed, 0.999 for moderately skewed.")


🗑️ Dropped dummy _missing columns from train and test.
✂️ 0 ultra-skewed features (clip at 0.5%–99.5%).
✂️ 57 moderately-skewed features (clip at 0.1%–99.9%).
✅ Adaptive clipping complete: 0.995 for ultra-skewed, 0.999 for moderately skewed.


In [ ]:
# Define columns to drop
year_built_cols = [f'year_built_{year}' for year in range(2015, 2020)]

# Drop if columns exist
train_merged.drop(columns=[col for col in year_built_cols if col in train_merged.columns], inplace=True)
test_merged.drop(columns=[col for col in year_built_cols if col in test_merged.columns], inplace=True)

print(" Dropped year_built_2015 to year_built_2019 from both train and test sets.")

✅ Dropped year_built_2015 to year_built_2019 from both train and test sets.


In [50]:
if "TARGET" in train_merged.columns:
    train_merged.drop("TARGET", axis=1,inplace=True)
else:
    print("TARGET not found in columns:", train_merged.columns.tolist())


In [ ]:
# Drop floor_area_total_final if it exists
for df_name, df in [('train_merged', train_merged), ('test_merged', test_merged)]:
    if 'floor_area_total_final' in df.columns:
        df.drop(columns='floor_area_total_final', inplace=True)
        print(f" Dropped 'floor_area_total_final' from {df_name}")
    else:
        print(f"ℹ 'floor_area_total_final' not found in {df_name}")


ℹ️ 'floor_area_total_final' not found in train_merged
ℹ️ 'floor_area_total_final' not found in test_merged


In [ ]:
train_cols = set(train_merged.columns)
test_cols = set(test_merged.columns)

missing_in_test = train_cols - test_cols
missing_in_train = test_cols - train_cols

print(" Columns in train but not in test:")
print(sorted(missing_in_test))

print("\n Columns in test but not in train:")
print(sorted(missing_in_train))


✅ Columns in train but not in test:
[]

❌ Columns in test but not in train:
[]


In [53]:
# Check if column sets match
print(set(train_merged.columns) == set(test_merged.columns))  # Should be True

# Check if column order matches
print(list(train_merged.columns) == list(test_merged.columns))  # Must also be True


True
True


In [54]:
import numpy as np
import pandas as pd
import optuna
import lightgbm as lgb
import shap
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error
from optuna.integration import LightGBMPruningCallback
from optuna.pruners import SuccessiveHalvingPruner
from lightgbm import log_evaluation, early_stopping

# === STEP 0: Setup Data ===
X_full = train_merged.copy()
y_full = pd.Series(y_train)
X_test = test_merged.copy()

# Detect categorical columns
cat_cols = X_full.select_dtypes(include=['category', 'object']).columns.tolist()
for col in cat_cols:
    X_full[col] = X_full[col].astype("category")
    X_test[col] = X_test[col].astype("category")

global_oof_preds = np.zeros(len(X_full))
best_score = float('inf')

# === STEP 1: Define Optuna Objective ===
def objective(trial):
    global global_oof_preds, best_score

    params = {
        "objective": "regression",
        "metric": "rmse",
        "boosting_type": "gbdt",
        "learning_rate": trial.suggest_float("learning_rate", 0.025, 0.04, log=True),
        "num_leaves": trial.suggest_int("num_leaves", 160, 220),
        "max_depth": trial.suggest_int("max_depth", 7, 11),
        "min_child_samples": trial.suggest_int("min_child_samples", 18, 30),
        "subsample": trial.suggest_float("subsample", 0.65, 0.88),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 0.75),
        "reg_alpha": trial.suggest_float("reg_alpha", 1.0, 5.0, log=True),
        "reg_lambda": trial.suggest_float("reg_lambda", 1.0, 4.0, log=True),
        "min_split_gain": trial.suggest_float("min_split_gain", 0.15, 0.25),
        "verbose": -1,
        "n_jobs": -1,
    }

    kf = KFold(n_splits=3, shuffle=True, random_state=42)
    val_rmse = []
    oof_preds = np.zeros(len(X_full))

    for fold, (train_idx, val_idx) in enumerate(kf.split(X_full)):
        X_train, X_val = X_full.iloc[train_idx], X_full.iloc[val_idx]
        y_train_fold, y_val = y_full.iloc[train_idx], y_full.iloc[val_idx]

        dtrain = lgb.Dataset(X_train, label=y_train_fold, categorical_feature=cat_cols)
        dvalid = lgb.Dataset(X_val, label=y_val, categorical_feature=cat_cols)

        model = lgb.train(
            params,
            dtrain,
            valid_sets=[dvalid],
            num_boost_round=1000,
            callbacks=[
                early_stopping(stopping_rounds=100),
                log_evaluation(period=100),
                LightGBMPruningCallback(trial, "rmse")
            ]
        )

        val_pred = model.predict(X_val, num_iteration=model.best_iteration)
        oof_preds[val_idx] = val_pred
        val_rmse.append(root_mean_squared_error(y_val, val_pred))

    mean_rmse = np.mean(val_rmse)
    trial.set_user_attr("cv_rmse", mean_rmse)

    if mean_rmse < best_score:
        best_score = mean_rmse
        global_oof_preds[:] = oof_preds

    print(f" Trial {trial.number} | CV RMSE: {mean_rmse:,.2f}")
    return mean_rmse

# === STEP 2: Run Optuna ===
study = optuna.create_study(
    direction='minimize',
    study_name='lgbm_study_final_with_shap',
    storage='sqlite:///lgbm_study_final_with_shap.db',
    load_if_exists=True,
    pruner=SuccessiveHalvingPruner(min_resource=100, reduction_factor=2)
)
study.optimize(objective, n_trials=25, show_progress_bar=True)

print(" Best RMSE:", study.best_value)
print(" Best Parameters:", study.best_params)
np.save("oof_preds_lgbm.npy", global_oof_preds)
print(" Saved: oof_preds_lgbm.npy")

# === STEP 3: SHAP + GAIN Feature Selection ===
kf = KFold(n_splits=3, shuffle=True, random_state=42)
selected_feature_sets = []

for fold, (train_idx, val_idx) in enumerate(kf.split(X_full)):
    X_train_raw, y_train_fold = X_full.iloc[train_idx], y_full.iloc[train_idx]

    train_dataset = lgb.Dataset(X_train_raw, label=y_train_fold, categorical_feature=cat_cols)
    model_temp = lgb.train(
        study.best_params,
        train_dataset,
        num_boost_round=200,
        valid_sets=[train_dataset],
        callbacks=[log_evaluation(period=100)] 
    )

    # SHAP importance
    explainer = shap.TreeExplainer(model_temp)
    shap_values = explainer.shap_values(X_train_raw)
    shap_df = pd.DataFrame(np.abs(shap_values), columns=X_train_raw.columns)
    shap_importance = shap_df.mean().sort_values(ascending=False)
    shap_cumsum = shap_importance.cumsum() / shap_importance.sum()
    top_shap = shap_cumsum[shap_cumsum <= 0.95].index.tolist()

    # Gain importance
    gain_importance = pd.Series(model_temp.feature_importance(importance_type='gain'), index=X_train_raw.columns)
    gain_sorted = gain_importance.sort_values(ascending=False)
    gain_cumsum = gain_sorted.cumsum() / gain_sorted.sum()
    top_gain = gain_cumsum[gain_cumsum <= 0.95].index.tolist()

    selected_features = list(set(top_shap).union(set(top_gain)))
    selected_feature_sets.append(selected_features)

# === STEP 4: Final Feature Union ===
final_union_features = list(set().union(*selected_feature_sets))
print(" Final Union Feature Count:", len(final_union_features))

# Filter only those categorical columns that are in final features
filtered_cat_cols = [col for col in cat_cols if col in final_union_features]

# === STEP 5: Final Model on Selected Features ===
X_full_selected = X_full[final_union_features]
X_test_selected = X_test[final_union_features]


final_dataset = lgb.Dataset(X_full_selected, label=y_full, categorical_feature=filtered_cat_cols)
final_model = lgb.train(
    study.best_params,
    final_dataset,
    num_boost_round=1000,
    valid_sets=[final_dataset],
    valid_names=["train"],
    callbacks=[log_evaluation(period=100)]
)

# === STEP 6: Predict on Test Set ===
test_preds = final_model.predict(X_test_selected, num_iteration=final_model.best_iteration)
np.save("test_preds_lgbm_shap.npy", test_preds)
print(" Saved: test_preds_lgbm_shap.npy")

# === STEP 7: Save Submission ===
submission = pd.DataFrame({
    'ACCOUNT': acct_test.values.ravel(),  # Replace with your ID col
    'TARGET': test_preds
})
submission.to_csv("submission_lgbm_shap.csv", index=False)
print(" Submission saved: submission_lgbm_shap.csv")

/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[I 2025-05-21 06:12:57,615] A new study created in RDB with name: lgbm_study_final_with_shap
  0%|          | 0/25 [00:00<?, ?it/s]

Training until validation scores don't improve for 100 rounds
[100]	valid_0's rmse: 42644
[200]	valid_0's rmse: 39953.4
[300]	valid_0's rmse: 39753.4
[400]	valid_0's rmse: 39603.1
[500]	valid_0's rmse: 39490.7
[600]	valid_0's rmse: 39387.7
[700]	valid_0's rmse: 39298.3
[800]	valid_0's rmse: 39229.7
[900]	valid_0's rmse: 39154.3
[1000]	valid_0's rmse: 39088.6
Did not meet early stopping. Best iteration is:
[999]	valid_0's rmse: 39088


/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(


Training until validation scores don't improve for 100 rounds


/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 5 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/

...

/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 900 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 901 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 902 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 903 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 904 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Pytho

[1000]	valid_0's rmse: 47482.3
Did not meet early stopping. Best iteration is:
[999]	valid_0's rmse: 47480


Best trial: 0. Best value: 41204.3: 100%|██████████| 25/25 [46:27<00:00, 111.49s/it]

📉 Trial 24 | CV RMSE: 41,368.74
[I 2025-05-21 06:59:24,844] Trial 24 finished with value: 41368.737424700535 and parameters: {'learning_rate': 0.03523781685901837, 'num_leaves': 220, 'max_depth': 11, 'min_child_samples': 26, 'subsample': 0.8403536627344244, 'colsample_bytree': 0.7141580570208755, 'reg_alpha': 2.045336154849232, 'reg_lambda': 1.0784119087472819, 'min_split_gain': 0.17069174630549644}. Best is trial 0 with value: 41204.31262134961.


✅ Best RMSE: 41204.31262134961
✅ Best Parameters: {'learning_rate': 0.039730220495763816, 'num_leaves': 210, 'max_depth': 11, 'min_child_samples': 18, 'subsample': 0.8602930077632327, 'colsample_bytree': 0.6962834149319597, 'reg_alpha': 4.731216779813845, 'reg_lambda': 1.7984216897061351, 'min_split_gain': 0.24840445491683466}
📁 Saved: oof_preds_lgbm.npy
[100]	training's l2: 1.4004e+09
[200]	training's l2: 8.47778e+08
[100]	training's l2: 1.34942e+09
[200]	training's l2: 8.13923e+08
[100]	training's l2: 1.18705e+09
[200]	training's l2: 7.70703e+08
✅ Final Union Feature Count: 60
[100]	train's l2: 1.29808e+09
[200]	train's l2: 8.24013e+08
[300]	train's l2: 6.53762e+08
[400]	train's l2: 5.48705e+08
[500]	train's l2: 4.75295e+08
[600]	train's l2: 4.1779e+08
[700]	train's l2: 3.76047e+08
[800]	train's l2: 3.38444e+08
[900]	train's l2: 3.08479e+08
[1000]	train's l2: 2.84088e+08
📁 Saved: test_preds_lgbm_shap.npy
📤 Submission saved: submission_lgbm_shap.csv


In [55]:
import numpy as np
import pandas as pd
import optuna
from xgboost import XGBRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error
from optuna.integration import XGBoostPruningCallback
from shap import TreeExplainer

# === STEP 0: Prepare Data ===
X_full = train_merged.copy()
y_full = pd.Series(y_train)
X_test = test_merged.copy()

bin_cols = [
    'building_value_growth_bin',
    'assessed_growth_bin',
    'land_value_growth_bin','year_built_bin'
]

for col in bin_cols:
    X_full[col] = X_full[col].cat.codes
    X_test[col] = X_test[col].cat.codes

categorical_cols = X_full.select_dtypes(include='object').columns.tolist()
X_full[categorical_cols] = X_full[categorical_cols].astype('category')
X_test[categorical_cols] = X_test[categorical_cols].astype('category')

# === Global OOF Tracker ===
global_oof_preds = np.zeros(len(X_full))
best_score = float("inf")

# === STEP 1: Optuna Objective Function (No SHAP during tuning) ===
def objective(trial):
    global global_oof_preds, best_score

    params = {
        "objective": "reg:squarederror",
        "eval_metric": "rmse",
        "tree_method": "hist",
        "learning_rate": trial.suggest_float("learning_rate", 0.047, 0.05, log=True),
        "max_depth": 6,
        "min_child_weight": trial.suggest_int("min_child_weight", 11, 12),
        "subsample": trial.suggest_float("subsample", 0.87, 0.89),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.7, 0.74),
        "reg_alpha": trial.suggest_float("reg_alpha", 0.30, 0.56, log=True),
        "reg_lambda": trial.suggest_float("reg_lambda", 0.05, 0.11, log=True),
        "gamma": trial.suggest_float("gamma", 1.1, 4.3),
        "n_estimators": 1000,
        "n_jobs": -1,
        "enable_categorical": True,
    }

    kf = KFold(n_splits=3, shuffle=True, random_state=42)
    oof_preds = np.zeros(len(X_full))
    fold_rmse = []

    for fold, (train_idx, val_idx) in enumerate(kf.split(X_full)):
        X_train, y_train_fold = X_full.iloc[train_idx], y_full.iloc[train_idx]
        X_val, y_val = X_full.iloc[val_idx], y_full.iloc[val_idx]

        model = XGBRegressor(
            **params,
            early_stopping_rounds=100,
            callbacks=[XGBoostPruningCallback(trial, "validation_0-rmse"),
                       ]
        )
        model.fit(X_train, y_train_fold, eval_set=[(X_val, y_val)], verbose=100)

        val_pred = model.predict(X_val)
        oof_preds[val_idx] = val_pred
        fold_rmse.append(root_mean_squared_error(y_val, val_pred))

    mean_rmse = np.mean(fold_rmse)
    trial.set_user_attr("cv_rmse", mean_rmse)

    if mean_rmse < best_score:
        best_score = mean_rmse
        global_oof_preds[:] = oof_preds

    print(f" Trial {trial.number} | CV RMSE: {mean_rmse:,.2f}")
    return mean_rmse

# === STEP 2: Run Optuna ===
study = optuna.create_study(
    direction='minimize',
    study_name='xgbreg_optuna_final_no_shap',
    pruner=optuna.pruners.SuccessiveHalvingPruner(min_resource=100, reduction_factor=2)
)
study.optimize(objective, n_trials=25, show_progress_bar=True)

print(" Best RMSE:", study.best_value)
print(" Best Parameters:", study.best_params)
np.save("oof_preds_xgbreg.npy", global_oof_preds)
print(" Saved: oof_preds_xgbreg.npy")

# === STEP 3: Post-Optuna SHAP + Gain Feature Selection ===
kf = KFold(n_splits=3, shuffle=True, random_state=42)
selected_feature_sets = []

for fold, (train_idx, val_idx) in enumerate(kf.split(X_full)):
    X_train_raw, y_train_fold = X_full.iloc[train_idx], y_full.iloc[train_idx]

    model_temp = XGBRegressor(**study.best_params, n_estimators=200)
    model_temp.fit(X_train_raw, y_train_fold)

    # === SHAP Importance ===
    explainer = TreeExplainer(model_temp)
    shap_values = explainer.shap_values(X_train_raw)
    shap_df = pd.DataFrame(np.abs(shap_values), columns=X_train_raw.columns)
    shap_importance = shap_df.mean().sort_values(ascending=False)
    shap_cumsum = shap_importance.cumsum() / shap_importance.sum()
    top_shap = shap_cumsum[shap_cumsum <= 0.95].index.tolist()

    # === Gain Importance ===
    gain_importance = pd.Series(model_temp.feature_importances_, index=X_train_raw.columns)
    gain_sorted = gain_importance.sort_values(ascending=False)
    gain_cumsum = gain_sorted.cumsum() / gain_sorted.sum()
    top_gain = gain_cumsum[gain_cumsum <= 0.95].index.tolist()

    selected_features = list(set(top_shap).union(set(top_gain)))
    selected_feature_sets.append(selected_features)

# === STEP 4: Final Feature Union ===
final_union_features = list(set().union(*selected_feature_sets))
print(" Final Union Feature Count:", len(final_union_features))

# === STEP 5: Train Final Model with Early Stopping on Union Features ===
X_full_selected = X_full[final_union_features]
X_test_selected = X_test[final_union_features]

final_model = XGBRegressor(**study.best_params)
final_model.set_params(n_estimators=1000, verbosity=1, early_stopping_rounds=100)
final_model.fit(X_full_selected, y_full, eval_set=[(X_full_selected, y_full)], verbose=100)

# === STEP 6: Predict on Test Set ===
test_preds = final_model.predict(X_test_selected)
np.save("test_preds_xgbreg.npy", test_preds)
print(" Saved: test_preds_xgbreg.npy")

# === STEP 7: Create Submission File ===
account_ids = acct_test.values.ravel()  # Replace with actual ID column
submission = pd.DataFrame({
    'ACCOUNT': account_ids,
    'TARGET': test_preds
})
submission.to_csv("submission_xgbreg.csv", index=False)
print(" Submission saved: submission_xgbreg.csv")


[I 2025-05-21 08:49:11,193] A new study created in memory with name: xgbreg_optuna_final_no_shap
  0%|          | 0/25 [00:00<?, ?it/s]

[0]	validation_0-rmse:298008.09165
[100]	validation_0-rmse:43291.66107
[200]	validation_0-rmse:41955.74571
[300]	validation_0-rmse:41342.78856
[400]	validation_0-rmse:40694.30373
[500]	validation_0-rmse:40257.10117
[600]	validation_0-rmse:39941.51384
[700]	validation_0-rmse:39659.15918
[800]	validation_0-rmse:39490.57387
[900]	validation_0-rmse:39309.40731
[999]	validation_0-rmse:39178.99984
[0]	validation_0-rmse:301343.55001


/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/

[100]	validation_0-rmse:43633.89491


/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 100 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 101 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 102 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 103 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 104 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Pytho

...

/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 900 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 901 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 902 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 903 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 904 is already reported.
  warnings.warn(
/Users/Srijith97/Library/Pytho

[999]	validation_0-rmse:46006.11736


/Users/Srijith97/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:497: UserWarning: The reported value is ignored because this `step` 999 is already reported.
  warnings.warn(
Best trial: 7. Best value: 40980.9: 100%|██████████| 25/25 [1:14:33<00:00, 178.95s/it]

 Trial 24 | CV RMSE: 41,122.67
[I 2025-05-21 10:03:44,905] Trial 24 finished with value: 41122.671875 and parameters: {'learning_rate': 0.04775969184158978, 'min_child_weight': 11, 'subsample': 0.8864709507691806, 'colsample_bytree': 0.7287450806475548, 'reg_alpha': 0.3330835373597742, 'reg_lambda': 0.06730794122465343, 'gamma': 2.119827910421352}. Best is trial 7 with value: 40980.930989583336.
 Best RMSE: 40980.930989583336
 Best Parameters: {'learning_rate': 0.04720857261312059, 'min_child_weight': 11, 'subsample': 0.8886675210033114, 'colsample_bytree': 0.7269521202249652, 'reg_alpha': 0.3033016426842381, 'reg_lambda': 0.07450056363162388, 'gamma': 1.9947747256925998}
 Saved: oof_preds_xgbreg.npy


 Final Union Feature Count: 112
[0]	validation_0-rmse:302184.48445
[100]	validation_0-rmse:38617.83791
[200]	validation_0-rmse:34073.80065
[300]	validation_0-rmse:31526.93363
[400]	validation_0-rmse:29586.13995
[500]	validation_0-rmse:28104.49179
[600]	validation_0-rmse:26872.00274
[700]	validation_0-rmse:25883.70149
[800]	validation_0-rmse:24981.54000
[900]	validation_0-rmse:24182.99681
[999]	validation_0-rmse:23498.29818
 Saved: test_preds_xgbreg.npy
 Submission saved: submission_xgbreg.csv


In [ ]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

# === Compute Residuals ===
residuals = y_full - global_oof_preds
res_df = X_full.copy()
res_df["actual"] = y_full
res_df["predicted"] = global_oof_preds
res_df["residual"] = residuals

# === Protest Count (2015–2018) ===
protest_cols = [f"protested_{year}" for year in range(2015, 2019)]
if all(col in res_df.columns for col in protest_cols):
    res_df["protest_count"] = res_df[protest_cols].sum(axis=1)

# === Plot 1: Residuals vs Actual Value ===
plt.figure(figsize=(8, 6))
sns.scatterplot(data=res_df, x="actual", y="residual", alpha=0.3)
plt.axhline(0, color="red", linestyle="--")
plt.title("Residuals vs. Actual Value")
plt.xlabel("Actual Value")
plt.ylabel("Residual (Actual - Predicted)")
plt.tight_layout()
plt.savefig("residuals_vs_actual_value.png", dpi=300)
plt.close()

# === Plot 2: Residuals by Protest Count ===
if "protest_count" in res_df.columns:
    plt.figure(figsize=(8, 6))
    sns.boxplot(x="protest_count", y="residual", data=res_df)
    plt.axhline(0, color="red", linestyle="--")
    plt.title("Residuals by Protest Count (2015–2018)")
    plt.xlabel("Number of Years Protested")
    plt.ylabel("Residual")
    plt.tight_layout()
    plt.savefig("residuals_by_protest_count.png", dpi=300)
    plt.close()

# === Plot 3: Residuals vs. Neighborhood Frequency ===
if "neighborhood_freq" in res_df.columns:
    plt.figure(figsize=(8, 6))
    sns.scatterplot(x="neighborhood_freq", y="residual", data=res_df, alpha=0.3)
    plt.axhline(0, color="red", linestyle="--")
    plt.title("Residuals vs. Neighborhood Frequency")
    plt.xlabel("Neighborhood Frequency")
    plt.ylabel("Residual")
    plt.tight_layout()
    plt.savefig("residuals_vs_neighborhood_freq.png", dpi=300)
    plt.close()


In [ ]:
import numpy as np
import pandas as pd
import shap
import matplotlib.pyplot as plt

# === SHAP Setup ===
explainer = shap.TreeExplainer(final_model)
shap_values = explainer.shap_values(X_full_selected)

# === SHAP DataFrame ===
shap_df = pd.DataFrame(np.abs(shap_values), columns=X_full_selected.columns)
shap_means = shap_df.mean().sort_values(ascending=False)
shap_importance_df = shap_means.reset_index()
shap_importance_df.columns = ["feature", "mean_shap"]

# === SHAP Summary Plot: Top 30 ===
plt.figure()
shap.summary_plot(shap_values, X_full_selected, max_display=30, show=False)
plt.tight_layout()
plt.savefig("shap_summary_top30_union.png", dpi=300)
plt.close()

# === SHAP Summary Plot: Bottom 30 ===
bottom_features = shap_importance_df.tail(30)["feature"].tolist()
shap.summary_plot(
    shap_values[:, [X_full_selected.columns.get_loc(f) for f in bottom_features]],
    X_full_selected[bottom_features],
    show=False
)
plt.tight_layout()
plt.savefig("shap_summary_bottom30_union.png", dpi=300)
plt.close()


AttributeError: 'XGBRegressor' object has no attribute 'feature_importance'